# Classification des Micro-régions de Corse par K-NN

Ce notebook implémente un système de classification des micro-régions corses basé sur l'algorithme des k plus proches voisins (k-NN). Cliquez sur la carte pour identifier la micro-région correspondante.

In [ ]:
# Installation des bibliothèques nécessaires
!pip install folium pandas numpy scikit-learn geopy --quiet

In [ ]:
import pandas as pd
import numpy as np
import folium
from folium import plugins
from sklearn.neighbors import KNeighborsClassifier
from geopy.geocoders import Nominatim
from geopy.extra.rate_limiter import RateLimiter
import time
from IPython.display import display, HTML
import json

## 1. Chargement et préparation des données

In [ ]:
# Chargement du fichier CSV
df = pd.read_csv('communes-par-territoire-de-projet-de-la-collectivite-territoriale-de-corse0.csv', 
                 sep=';', encoding='utf-8')

print(f"Nombre de communes: {len(df)}")
print("\nPremières lignes:")
display(df.head())
print("\nTerritoires de projet (micro-régions):")
print(df['Territoire de projet'].unique())

## 2. Géocodage des communes

Si le fichier ne contient pas déjà les coordonnées GPS, nous les récupérons via géocodage.

In [ ]:
# Fonction pour obtenir les coordonnées GPS d'une commune
def geocode_commune(commune, departement, code_postal):
    """
    Géocode une commune corse pour obtenir ses coordonnées GPS
    """
    geolocator = Nominatim(user_agent="corse_knn_classifier")
    
    try:
        # Essai avec le nom de la commune et Corse
        query = f"{commune}, Corse, France"
        location = geolocator.geocode(query, timeout=10)
        
        if location:
            return location.latitude, location.longitude
        
        # Essai avec le code postal
        query = f"{commune}, {code_postal}, France"
        location = geolocator.geocode(query, timeout=10)
        
        if location:
            return location.latitude, location.longitude
            
    except Exception as e:
        print(f"Erreur pour {commune}: {e}")
    
    return None, None

# Vérifier si les colonnes GPS existent déjà
if 'Latitude' not in df.columns or 'Longitude' not in df.columns:
    print("Géocodage des communes en cours... (cela peut prendre quelques minutes)")
    
    # Géocodage avec rate limiting pour respecter les limites de l'API
    latitudes = []
    longitudes = []
    
    for idx, row in df.iterrows():
        lat, lon = geocode_commune(row['Commune'], row['Département'], row['Code Postal'])
        latitudes.append(lat)
        longitudes.append(lon)
        
        # Affichage de la progression
        if (idx + 1) % 10 == 0:
            print(f"Progression: {idx + 1}/{len(df)} communes géocodées")
        
        # Pause pour respecter les limites de l'API
        time.sleep(1.5)
    
    df['Latitude'] = latitudes
    df['Longitude'] = longitudes
    
    # Sauvegarde du dataframe avec coordonnées
    df.to_csv('communes_corse_avec_gps.csv', sep=';', index=False, encoding='utf-8')
    print("\nGéocodage terminé et sauvegardé dans 'communes_corse_avec_gps.csv'")
else:
    print("Les coordonnées GPS sont déjà présentes dans le fichier.")

# Supprimer les lignes sans coordonnées
df_clean = df.dropna(subset=['Latitude', 'Longitude']).copy()
print(f"\nCommunes avec coordonnées GPS: {len(df_clean)}/{len(df)}")

## 3. Entraînement du modèle k-NN

In [ ]:
# Préparation des données pour k-NN
X = df_clean[['Latitude', 'Longitude']].values
y = df_clean['Territoire de projet'].values

# Création du modèle k-NN avec k=5 (ajustable)
k = 5
knn = KNeighborsClassifier(n_neighbors=k, weights='distance', metric='haversine')

# Conversion des coordonnées en radians pour la distance haversine
X_rad = np.radians(X)

# Entraînement du modèle
knn.fit(X_rad, y)

print(f"Modèle k-NN entraîné avec k={k} voisins")
print(f"Nombre de micro-régions: {len(np.unique(y))}")
print(f"Micro-régions: {sorted(np.unique(y))}")

## 4. Création de la carte interactive avec Folium

In [ ]:
# Couleurs pour chaque micro-région
microregions = sorted(df_clean['Territoire de projet'].unique())
colors = ['red', 'blue', 'green', 'purple', 'orange', 'darkred', 
          'lightred', 'beige', 'darkblue', 'darkgreen', 'cadetblue', 
          'darkpurple', 'pink', 'lightblue', 'lightgreen', 'gray', 'black', 'lightgray']

color_map = {region: colors[i % len(colors)] for i, region in enumerate(microregions)}

print("Carte des couleurs par micro-région:")
for region, color in color_map.items():
    print(f"  {region}: {color}")

In [ ]:
# Coordonnées du centre de la Corse
center_lat = df_clean['Latitude'].mean()
center_lon = df_clean['Longitude'].mean()

# Création de la carte
m = folium.Map(
    location=[center_lat, center_lon],
    zoom_start=9,
    tiles='OpenStreetMap'
)

# Ajout des marqueurs pour chaque commune
for idx, row in df_clean.iterrows():
    folium.CircleMarker(
        location=[row['Latitude'], row['Longitude']],
        radius=3,
        popup=f"<b>{row['Commune']}</b><br>{row['Territoire de projet']}",
        tooltip=row['Commune'],
        color=color_map[row['Territoire de projet']],
        fill=True,
        fillColor=color_map[row['Territoire de projet']],
        fillOpacity=0.7
    ).add_to(m)

# Ajout d'une légende
legend_html = '''
<div style="position: fixed; 
            top: 10px; right: 10px; width: 250px; height: auto; 
            background-color: white; border:2px solid grey; z-index:9999; 
            font-size:12px; padding: 10px">
<p style="margin-bottom: 5px;"><b>Micro-régions de Corse</b></p>
'''

for region, color in sorted(color_map.items()):
    legend_html += f'<p style="margin: 3px 0;"><i class="fa fa-circle" style="color:{color}"></i> {region}</p>'

legend_html += '</div>'

m.get_root().html.add_child(folium.Element(legend_html))

# Ajout du plugin de clic
# Note: Folium ne supporte pas nativement l'interactivité côté Python en temps réel
# Nous allons créer une version avec JavaScript pour la prédiction

print("Carte de base créée avec les communes colorées par micro-région")

## 5. Carte interactive avec prédiction au clic

Cette version utilise JavaScript pour permettre de cliquer sur la carte et afficher la micro-région prédite.

In [ ]:
# Création d'une nouvelle carte avec interaction JavaScript
m_interactive = folium.Map(
    location=[center_lat, center_lon],
    zoom_start=9,
    tiles='OpenStreetMap'
)

# Ajout des communes
for idx, row in df_clean.iterrows():
    folium.CircleMarker(
        location=[row['Latitude'], row['Longitude']],
        radius=3,
        popup=f"<b>{row['Commune']}</b><br>{row['Territoire de projet']}",
        tooltip=row['Commune'],
        color=color_map[row['Territoire de projet']],
        fill=True,
        fillColor=color_map[row['Territoire de projet']],
        fillOpacity=0.7
    ).add_to(m_interactive)

# Préparer les données des communes pour JavaScript
communes_data = df_clean[['Latitude', 'Longitude', 'Commune', 'Territoire de projet']].to_dict('records')

# JavaScript pour la prédiction k-NN au clic
click_js = f"""
<script>
// Données des communes
var communesData = {json.dumps(communes_data)};

// Carte des couleurs
var colorMap = {json.dumps(color_map)};

// Fonction pour calculer la distance haversine
function haversineDistance(lat1, lon1, lat2, lon2) {{
    const R = 6371; // Rayon de la Terre en km
    const dLat = (lat2 - lat1) * Math.PI / 180;
    const dLon = (lon2 - lon1) * Math.PI / 180;
    const a = Math.sin(dLat/2) * Math.sin(dLat/2) +
              Math.cos(lat1 * Math.PI / 180) * Math.cos(lat2 * Math.PI / 180) *
              Math.sin(dLon/2) * Math.sin(dLon/2);
    const c = 2 * Math.atan2(Math.sqrt(a), Math.sqrt(1-a));
    return R * c;
}}

// Fonction k-NN
function predictRegion(lat, lon, k) {{
    // Calculer les distances
    var distances = communesData.map(function(commune) {{
        return {{
            distance: haversineDistance(lat, lon, commune.Latitude, commune.Longitude),
            region: commune['Territoire de projet'],
            commune: commune.Commune
        }};
    }});
    
    // Trier par distance
    distances.sort((a, b) => a.distance - b.distance);
    
    // Prendre les k plus proches
    var kNearest = distances.slice(0, k);
    
    // Vote pondéré par l'inverse de la distance
    var votes = {{}};
    kNearest.forEach(function(neighbor) {{
        var weight = 1 / (neighbor.distance + 0.001); // +0.001 pour éviter division par 0
        if (votes[neighbor.region]) {{
            votes[neighbor.region] += weight;
        }} else {{
            votes[neighbor.region] = weight;
        }}
    }});
    
    // Trouver la région gagnante
    var maxVote = 0;
    var predictedRegion = '';
    for (var region in votes) {{
        if (votes[region] > maxVote) {{
            maxVote = votes[region];
            predictedRegion = region;
        }}
    }}
    
    return {{
        region: predictedRegion,
        neighbors: kNearest
    }};
}}

// Variable pour stocker le marqueur de prédiction
var predictionMarker = null;
var neighborLines = [];

// Attendre que la carte soit chargée
setTimeout(function() {{
    var maps = document.querySelectorAll('.folium-map');
    if (maps.length > 0) {{
        var mapElement = maps[maps.length - 1];
        var leafletMap = mapElement._leaflet_map;
        
        if (leafletMap) {{
            leafletMap.on('click', function(e) {{
                var lat = e.latlng.lat;
                var lon = e.latlng.lng;
                
                // Prédiction avec k={k}
                var result = predictRegion(lat, lon, {k});
                
                // Supprimer l'ancien marqueur et lignes
                if (predictionMarker) {{
                    leafletMap.removeLayer(predictionMarker);
                }}
                neighborLines.forEach(function(line) {{
                    leafletMap.removeLayer(line);
                }});
                neighborLines = [];
                
                // Créer le popup avec informations détaillées
                var popupContent = '<div style="min-width: 200px;">' +
                    '<h4 style="margin: 5px 0;">Prédiction k-NN</h4>' +
                    '<p style="margin: 5px 0;"><b>Micro-région:</b> ' + result.region + '</p>' +
                    '<p style="margin: 5px 0;"><b>Coordonnées:</b><br>' + 
                    'Lat: ' + lat.toFixed(5) + '<br>Lon: ' + lon.toFixed(5) + '</p>' +
                    '<p style="margin: 5px 0;"><b>{k} plus proches communes:</b></p>' +
                    '<ul style="margin: 5px 0; padding-left: 20px; font-size: 11px;">';
                
                result.neighbors.forEach(function(neighbor) {{
                    popupContent += '<li>' + neighbor.commune + 
                        ' (' + neighbor.distance.toFixed(2) + ' km)</li>';
                }});
                
                popupContent += '</ul></div>';
                
                // Ajouter le nouveau marqueur
                predictionMarker = L.marker([lat, lon], {{
                    icon: L.divIcon({{
                        className: 'prediction-marker',
                        html: '<div style="background-color: ' + colorMap[result.region] + 
                              '; width: 20px; height: 20px; border-radius: 50%; ' +
                              'border: 3px solid white; box-shadow: 0 0 10px rgba(0,0,0,0.5);"></div>',
                        iconSize: [20, 20]
                    }})
                }}).addTo(leafletMap);
                
                predictionMarker.bindPopup(popupContent).openPopup();
                
                // Ajouter des lignes vers les k plus proches voisins
                result.neighbors.forEach(function(neighbor) {{
                    var commune = communesData.find(c => c.Commune === neighbor.commune);
                    if (commune) {{
                        var line = L.polyline(
                            [[lat, lon], [commune.Latitude, commune.Longitude]],
                            {{
                                color: 'gray',
                                weight: 1,
                                opacity: 0.5,
                                dashArray: '5, 5'
                            }}
                        ).addTo(leafletMap);
                        neighborLines.push(line);
                    }}
                }});
            }});
            
            console.log('Gestionnaire de clic k-NN activé');
        }}
    }}
}}, 1000);
</script>
"""

m_interactive.get_root().html.add_child(folium.Element(click_js))

# Ajout de la légende
m_interactive.get_root().html.add_child(folium.Element(legend_html))

# Ajout d'instructions
instructions_html = '''
<div style="position: fixed; 
            bottom: 10px; left: 10px; width: 300px; 
            background-color: white; border:2px solid grey; z-index:9999; 
            font-size:13px; padding: 10px">
<p style="margin: 0;"><b>🖱️ Instructions:</b></p>
<p style="margin: 5px 0;">Cliquez n'importe où sur la carte pour prédire la micro-région à partir de l'algorithme k-NN.</p>
<p style="margin: 5px 0;">Les lignes pointillées montrent les k plus proches communes utilisées pour la prédiction.</p>
</div>
'''

m_interactive.get_root().html.add_child(folium.Element(instructions_html))

print("Carte interactive créée avec succès!")
print(f"\nCliquez sur n'importe quel point de la carte pour prédire sa micro-région avec k={k} voisins.")

In [ ]:
# Affichage de la carte interactive
m_interactive

## 6. Sauvegarde de la carte

In [ ]:
# Sauvegarder la carte interactive
m_interactive.save('carte_corse_knn_interactive.html')
print("Carte sauvegardée dans 'carte_corse_knn_interactive.html'")
print("Vous pouvez ouvrir ce fichier dans un navigateur pour une utilisation autonome.")

## 7. Test de la prédiction (optionnel)

In [ ]:
# Fonction pour tester la prédiction sur des coordonnées spécifiques
def predict_region(lat, lon, k_value=5):
    """
    Prédit la micro-région pour des coordonnées données
    """
    # Conversion en radians
    coords_rad = np.radians([[lat, lon]])
    
    # Prédiction
    prediction = knn.predict(coords_rad)[0]
    
    # Trouver les k plus proches voisins
    distances, indices = knn.kneighbors(coords_rad)
    
    # Convertir les distances de radians en km
    distances_km = distances[0] * 6371  # Rayon de la Terre en km
    
    print(f"\n📍 Coordonnées: {lat:.5f}, {lon:.5f}")
    print(f"🎯 Micro-région prédite: {prediction}")
    print(f"\n{k_value} plus proches communes:")
    
    for i, idx in enumerate(indices[0]):
        commune_info = df_clean.iloc[idx]
        print(f"  {i+1}. {commune_info['Commune']} ({commune_info['Territoire de projet']}) - {distances_km[i]:.2f} km")
    
    return prediction

# Exemples de test
print("=" * 60)
print("TESTS DE PRÉDICTION")
print("=" * 60)

# Test 1: Centre approximatif de la Corse
predict_region(42.15, 9.15, k)

# Test 2: Nord de la Corse (Balagne)
predict_region(42.55, 8.85, k)

# Test 3: Sud de la Corse
predict_region(41.65, 9.15, k)

## 8. Analyse de performance (optionnel)

In [ ]:
# Évaluation de la cohérence du modèle (cross-validation)
from sklearn.model_selection import cross_val_score

# Test avec différentes valeurs de k
k_values = [3, 5, 7, 9, 11]
scores = []

print("Évaluation de la précision pour différentes valeurs de k:\n")

for k_val in k_values:
    knn_temp = KNeighborsClassifier(n_neighbors=k_val, weights='distance', metric='haversine')
    cv_scores = cross_val_score(knn_temp, X_rad, y, cv=5)
    mean_score = cv_scores.mean()
    scores.append(mean_score)
    print(f"k={k_val:2d}: Précision moyenne = {mean_score:.3f} (+/- {cv_scores.std():.3f})")

# Visualisation simple
print(f"\n✨ Meilleure valeur de k: {k_values[scores.index(max(scores))]} (précision: {max(scores):.3f})")

## Conclusion

Ce notebook implémente un classificateur k-NN pour les micro-régions de Corse avec:
- ✅ Chargement et géocodage des communes corses
- ✅ Entraînement d'un modèle k-NN avec distance haversine
- ✅ Carte interactive Folium avec prédiction au clic
- ✅ Visualisation des k plus proches voisins
- ✅ Légende et instructions pour l'utilisateur

**Utilisation:**
1. Cliquez n'importe où sur la carte
2. Un marqueur coloré apparaît avec la micro-région prédite
3. Des lignes pointillées montrent les k communes les plus proches
4. Un popup détaille la prédiction et les voisins

La carte HTML peut être ouverte dans n'importe quel navigateur pour une utilisation autonome!